In [210]:
import urllib
import urllib3
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException
from selenium.webdriver.common.keys import Keys
import time
from bs4 import BeautifulSoup as bs
import os
import getpass
import re 
import glob
from pynput.keyboard import Key, Controller
import pandas as pd
import numpy as np

In [36]:
def getDriver():
    DRIVER_PATH = './chromedriver.exe'
    wd = webdriver.Chrome(executable_path=DRIVER_PATH)
    time.sleep(5)
    wd.get('https://www.usembassy.gov/#C')
    return wd

def getMainCountryURL(wd):
    main_country_list = wd.find_elements_by_xpath("//a[@class='pcs-post-title']")
    main_country_url = []
    embassy_url = []
    for i in main_country_list:
        main_country_url.append(i.get_attribute('href'))
    #main_country_url
    time.sleep(7)
    return main_country_url

def getCountryNamesCleaned(wd):
    country_ar = []
    country_temp = wd.page_source
    country_data = bs(country_temp, 'lxml')
    for strong_tag in country_data.find_all('li'):
        tester = strong_tag.find_all('a')
        for names in tester:
            pattern = re.compile(r'[//][a-z]{4,30}')
            for i in re.findall(pattern, str(names.get('href'))):
                country_ar.append(i)
    return country_ar

def getPostName(wd, country_url, post_urls):
    try:
        path = wd.find_element_by_xpath("//div[@class='cityname1']//a").get_attribute('href')
        for posts, url in enumerate(wd.find_elements_by_xpath("//div[@class='cityname1']//a")):
            post_urls[str(posts)] = url.get_attribute('href')
        wd.get(path)
    except NoSuchElementException:
        keyboard = Controller()
        keyboard.press(Key.ctrl)
        keyboard.press('r')
        keyboard.release(Key.ctrl)
        keyboard.release('r')
        time.sleep(5)
        path = wd.find_element_by_xpath("//div[@class='cityname1']//a").get_attribute('href')
        for posts, url in enumerate(wd.find_elements_by_xpath("//div[@class='cityname1']//a")):
            post_urls[str(posts)] = url.get_attribute('href')
        wd.get(path)
        
def getPostNamesCleaned(wd):
    consulate_dict = {}
    consulates = []
    for footer in wd.find_elements_by_xpath(".//div[@class='footer-middle']"):
        for widget in footer.find_elements_by_xpath(".//div[@class='textwidget']//a"):
            consulates.append(widget.get_attribute('href'))
    post_names = []
    for post_name in consulates:
        pattern = re.compile(r'[v][//].+[//]')
        for i in re.findall(pattern, str(post_name)):
            post_names.append(i)
    consulate_dict["Posts"] = post_names
    return consulate_dict

def getLanguages(wd):
    language_dict = {}
    language_arr = []
    try:
        wd.find_element_by_xpath("//i[@class='fa fa-plus-square']").click()
        languages = wd.find_elements_by_xpath("//div[@class='translations_sidebar']//li")
        for i in (languages):
            language_arr.append(i.text)
    except NoSuchElementException:
        language_arr.append('None')
    for i in range(0, len(language_arr)):
        if(language_arr[i] == 'None'):
            return
        else:
            language_dict[str(i)] = language_arr[i]
    return language_dict

def socialMediaDictionary(wd, post_names):
    social_dict = {}
    ret_dict = {}
    temp_arr = []
    final_arr = []
    x = 0
    for main in wd.find_elements_by_xpath(".//main"):

        for social in main.find_elements_by_xpath(".//div[@class='mo-social-links']"):
            social_arr = []
            for attrib in social.find_elements_by_xpath('.//a'):
                social_arr.append(attrib.get_attribute('href'))
            social_dict[x] = social_arr
            x+=1

    if(len(social_dict) == 0):
        for side in wd.find_elements_by_xpath("//div[@class='textbox-content']"):
            for social in side.find_elements_by_xpath(".//div[@class='mo-social-links']"):
                social_arr = []
                for attrib in social.find_elements_by_xpath('.//a'):
                    social_arr.append(attrib.get_attribute('href'))
                social_dict[x] = social_arr
                x+=1
    ret_dict["Social"] = social_dict
    return ret_dict

In [45]:
wd = getDriver()
main_country_url = getMainCountryURL(wd)
time.sleep(5)
#print(main_country_url)
clean_country_names = getCountryNamesCleaned(wd)
time.sleep(5)
#print(clean_country_names)
country_dict = {}
x = 0
for k,v in enumerate(main_country_url):
    country_name = {}
    post_names = []
    language_dict = {}
    consulate_level = {}
    social_dict = {}
    post_urls = {}

    # Access Embassy list
    country_url = wd.get(str(main_country_url[k]))
    time.sleep(5)

    # GET POST NAMES
    getPostName(wd,country_url, post_urls)
    
    time.sleep(5)
    post_names = getPostNamesCleaned(wd)
    #print(post_names)
    
    time.sleep(5)
    language_dict["Languages"] = getLanguages(wd)
    #print(language_dict)
    
    social_dict = socialMediaDictionary(wd, post_names)
    #print(social_dict)
    country_name["Country"] = main_country_url[k]
    
    country_dict[x] = dict(**country_name, **post_names, **language_dict, **social_dict, **post_urls)
    print(country_dict)
    time.sleep(5)
    x+=1
    
    
    #city_names_cleaned = getPostNamesCleaned(wd,city_websites)
    #print(city_names_cleaned)
    

{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}}
{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}, 1: {'Country': 'https://www.usembassy.gov/albania/', 'Posts': ['v/embassy/tirana/'], 'Languages': {'0': 'Shqip'}, 'Social': {0: ['https://twitter.com/USEmbassyTirana', 

{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}, 1: {'Country': 'https://www.usembassy.gov/albania/', 'Posts': ['v/embassy/tirana/'], 'Languages': {'0': 'Shqip'}, 'Social': {0: ['https://twitter.com/USEmbassyTirana', 'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837', 'http://www.youtube.com/USEmbassyTirana', 'http://instagram.com/usembassytirana', 'mailto:TiranaWebmaster@state.gov']}, '0': 'https://al.usembassy.gov/embassy/tirana/'}, 2: {'Country': 'https://www.usembassy.gov/algeria/', 'Posts': ['v/embassy/algiers/', 'v/contact-us/'], 'Languages': {'0': 'Français', '1': 'العربية'}, 'Social': {0: ['h

{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}, 1: {'Country': 'https://www.usembassy.gov/albania/', 'Posts': ['v/embassy/tirana/'], 'Languages': {'0': 'Shqip'}, 'Social': {0: ['https://twitter.com/USEmbassyTirana', 'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837', 'http://www.youtube.com/USEmbassyTirana', 'http://instagram.com/usembassytirana', 'mailto:TiranaWebmaster@state.gov']}, '0': 'https://al.usembassy.gov/embassy/tirana/'}, 2: {'Country': 'https://www.usembassy.gov/algeria/', 'Posts': ['v/embassy/algiers/', 'v/contact-us/'], 'Languages': {'0': 'Français', '1': 'العربية'}, 'Social': {0: ['h

{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}, 1: {'Country': 'https://www.usembassy.gov/albania/', 'Posts': ['v/embassy/tirana/'], 'Languages': {'0': 'Shqip'}, 'Social': {0: ['https://twitter.com/USEmbassyTirana', 'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837', 'http://www.youtube.com/USEmbassyTirana', 'http://instagram.com/usembassytirana', 'mailto:TiranaWebmaster@state.gov']}, '0': 'https://al.usembassy.gov/embassy/tirana/'}, 2: {'Country': 'https://www.usembassy.gov/algeria/', 'Posts': ['v/embassy/algiers/', 'v/contact-us/'], 'Languages': {'0': 'Français', '1': 'العربية'}, 'Social': {0: ['h

{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}, 1: {'Country': 'https://www.usembassy.gov/albania/', 'Posts': ['v/embassy/tirana/'], 'Languages': {'0': 'Shqip'}, 'Social': {0: ['https://twitter.com/USEmbassyTirana', 'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837', 'http://www.youtube.com/USEmbassyTirana', 'http://instagram.com/usembassytirana', 'mailto:TiranaWebmaster@state.gov']}, '0': 'https://al.usembassy.gov/embassy/tirana/'}, 2: {'Country': 'https://www.usembassy.gov/algeria/', 'Posts': ['v/embassy/algiers/', 'v/contact-us/'], 'Languages': {'0': 'Français', '1': 'العربية'}, 'Social': {0: ['h

...

{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}, 1: {'Country': 'https://www.usembassy.gov/albania/', 'Posts': ['v/embassy/tirana/'], 'Languages': {'0': 'Shqip'}, 'Social': {0: ['https://twitter.com/USEmbassyTirana', 'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837', 'http://www.youtube.com/USEmbassyTirana', 'http://instagram.com/usembassytirana', 'mailto:TiranaWebmaster@state.gov']}, '0': 'https://al.usembassy.gov/embassy/tirana/'}, 2: {'Country': 'https://www.usembassy.gov/algeria/', 'Posts': ['v/embassy/algiers/', 'v/contact-us/'], 'Languages': {'0': 'Français', '1': 'العربية'}, 'Social': {0: ['h

{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}, 1: {'Country': 'https://www.usembassy.gov/albania/', 'Posts': ['v/embassy/tirana/'], 'Languages': {'0': 'Shqip'}, 'Social': {0: ['https://twitter.com/USEmbassyTirana', 'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837', 'http://www.youtube.com/USEmbassyTirana', 'http://instagram.com/usembassytirana', 'mailto:TiranaWebmaster@state.gov']}, '0': 'https://al.usembassy.gov/embassy/tirana/'}, 2: {'Country': 'https://www.usembassy.gov/algeria/', 'Posts': ['v/embassy/algiers/', 'v/contact-us/'], 'Languages': {'0': 'Français', '1': 'العربية'}, 'Social': {0: ['h

{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}, 1: {'Country': 'https://www.usembassy.gov/albania/', 'Posts': ['v/embassy/tirana/'], 'Languages': {'0': 'Shqip'}, 'Social': {0: ['https://twitter.com/USEmbassyTirana', 'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837', 'http://www.youtube.com/USEmbassyTirana', 'http://instagram.com/usembassytirana', 'mailto:TiranaWebmaster@state.gov']}, '0': 'https://al.usembassy.gov/embassy/tirana/'}, 2: {'Country': 'https://www.usembassy.gov/algeria/', 'Posts': ['v/embassy/algiers/', 'v/contact-us/'], 'Languages': {'0': 'Français', '1': 'العربية'}, 'Social': {0: ['h

{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}, 1: {'Country': 'https://www.usembassy.gov/albania/', 'Posts': ['v/embassy/tirana/'], 'Languages': {'0': 'Shqip'}, 'Social': {0: ['https://twitter.com/USEmbassyTirana', 'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837', 'http://www.youtube.com/USEmbassyTirana', 'http://instagram.com/usembassytirana', 'mailto:TiranaWebmaster@state.gov']}, '0': 'https://al.usembassy.gov/embassy/tirana/'}, 2: {'Country': 'https://www.usembassy.gov/algeria/', 'Posts': ['v/embassy/algiers/', 'v/contact-us/'], 'Languages': {'0': 'Français', '1': 'العربية'}, 'Social': {0: ['h

{0: {'Country': 'https://www.usembassy.gov/afghanistan/', 'Posts': ['v/embassy/kabul/'], 'Languages': {'0': 'دری', '1': 'پښتو'}, 'Social': {0: ['http://www.twitter.com/usembassykabul', 'https://www.facebook.com/kabulusembassy/', 'http://www.youtube.com/usembassykabul1', 'https://www.flickr.com/photos/kabulpublicdiplomacy/', 'https://www.instagram.com/usembassykabul/']}, '0': 'https://af.usembassy.gov/embassy/'}, 1: {'Country': 'https://www.usembassy.gov/albania/', 'Posts': ['v/embassy/tirana/'], 'Languages': {'0': 'Shqip'}, 'Social': {0: ['https://twitter.com/USEmbassyTirana', 'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837', 'http://www.youtube.com/USEmbassyTirana', 'http://instagram.com/usembassytirana', 'mailto:TiranaWebmaster@state.gov']}, '0': 'https://al.usembassy.gov/embassy/tirana/'}, 2: {'Country': 'https://www.usembassy.gov/algeria/', 'Posts': ['v/embassy/algiers/', 'v/contact-us/'], 'Languages': {'0': 'Français', '1': 'العربية'}, 'Social': {0: ['h

In [12]:
country_dict

{0: {'Posts': ['v/embassy/kabul/'],
  'Language': ['دری', 'پښتو'],
  'Social': {0: ['http://www.twitter.com/usembassykabul',
    'https://www.facebook.com/kabulusembassy/',
    'http://www.youtube.com/usembassykabul1',
    'https://www.flickr.com/photos/kabulpublicdiplomacy/',
    'https://www.instagram.com/usembassykabul/']}},
 1: {'Posts': ['v/embassy/tirana/'],
  'Language': ['Shqip'],
  'Social': {0: ['https://twitter.com/USEmbassyTirana',
    'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837',
    'http://www.youtube.com/USEmbassyTirana',
    'http://instagram.com/usembassytirana',
    'mailto:TiranaWebmaster@state.gov']}},
 2: {'Posts': ['v/embassy/algiers/', 'v/contact-us/'],
  'Language': ['Français', 'العربية'],
  'Social': {0: ['http://twitter.com/USEmbAlgiers',
    'http://www.facebook.com/USEmbassyAlgiers',
    'http://www.youtube.com/user/USEmbassyAlgiers',
    'https://www.instagram.com/usembassyalgiers/'],
   1: ['https://twitter.com/USAmbtoAlge

In [277]:
len(clean_country_names)

182

In [281]:
country_dict["Country"] = clean_country_names

In [282]:
country_dict

{0: {'Language': ['دری', 'پښتو'],
  'Social': {0: ['http://www.twitter.com/usembassykabul',
    'https://www.facebook.com/kabulusembassy/',
    'http://www.youtube.com/usembassykabul1',
    'https://www.flickr.com/photos/kabulpublicdiplomacy/',
    'https://www.instagram.com/usembassykabul/']},
  'Posts': ['v/embassy/kabul/']},
 1: {'Language': ['Shqip'],
  'Social': {0: ['https://twitter.com/USEmbassyTirana',
    'http://www.facebook.com/pages/Tirana-Albania/US-Embassy-Tirana/74591195837',
    'http://www.youtube.com/USEmbassyTirana',
    'http://instagram.com/usembassytirana',
    'mailto:TiranaWebmaster@state.gov']},
  'Posts': ['v/embassy/tirana/']},
 2: {'Language': ['Français', 'العربية'],
  'Social': {0: ['http://twitter.com/USEmbAlgiers',
    'http://www.facebook.com/USEmbassyAlgiers',
    'http://www.youtube.com/user/USEmbassyAlgiers',
    'https://www.instagram.com/usembassyalgiers/'],
   1: ['https://twitter.com/USAmbtoAlgeria']},
  'Posts': ['v/embassy/algiers/', 'v/contact

In [46]:
import json

with open('app.json', 'w', encoding='utf8') as fp:
    json.dump(country_dict, fp, ensure_ascii=False, indent=4)

In [101]:
final_try = pd.read_json('app.json', orient='records', dtype=str)
final_try_transpose = final_try.T
final_try_transpose.columns = ['Country','Posts','Languages','Social','Post_Url_1','Post_Url_2','Post_Url_3','Post_Url_4','Post_Url_5','Post_Url_6','Post_Url_7','Post_Url_8','Post_Url_9','Post_Url_10']
final_try_transpose["Country_Url"] = final_try_transpose["Country"]
final_try_transpose["Country"] = final_try_transpose.Country.str.replace('https://www.usembassy.gov/','')
final_try_transpose["Country"] = final_try_transpose["Country"].str.title()
final_try_transpose["Country"] = final_try_transpose.Country.str.replace('/','')
final_try_transpose["Posts"] = final_try_transpose.Posts.str.replace('embassy-consulates','')
final_try_transpose["Posts"] = final_try_transpose.Posts.str.replace('embassy','')
final_try_transpose["Posts"] = final_try_transpose.Posts.str.replace('consulates','')
final_try_transpose["Posts"] = final_try_transpose.Posts.str.replace('v/','')
final_try_transpose.to_csv('test.csv')

In [82]:
final_try_transpose

Country                         Posts  \
0    Afghanistan                   ['/kabul/']   
1        Albania                  ['/tirana/']   
2        Algeria  ['/algiers/', 'contact-us/']   
3         Angola                  ['/luanda/']   
4      Argentina            ['/buenos-aires/']   
..           ...                           ...   
186    Venezuela                  ['interim/']   
187      Vietnam  ['//', '/ho-chi-minh-city/']   
188        Yemen                   ['/sanaa/']   
189       Zambia                        ['//']   
190     Zimbabwe                  ['/harare/']   

                             Languages  \
0            {'0': 'دری', '1': 'پښتو'}   
1                       {'0': 'Shqip'}   
2    {'0': 'Français', '1': 'العربية'}   
3                   {'0': 'Português'}   
4                     {'0': 'Español'}   
..                                 ...   
186                   {'0': 'Español'}   
187                {'0': 'Tiếng Việt'}   
188                   {'0': 'العربية'}   
189                                 {}   
190                                 {}   

                                                Social  \
0    {'0': ['http://www.twitter.com/usembassykabul'...   
1    {'0': ['https://twitter.com/USEmbassyTirana', ...   
2    {'0': ['http://twitter.com/USEmbAlgiers', 'htt...   
3    {'0': ['https://www.facebook.com/USinLuanda', ...   
4    {'0': ['http://twitter.com/EmbajadaEEUUarg', '...   
..                                                 ...   
186  {'0': ['http://twitter.com/usembassyve', 'http...   
187  {'0': ['https://www.facebook.com/usembassyhano...   
188  {'0': ['https://twitter.com/USEmbassyYemen', '...   
189  {'0': ['http://twitter.com/usembassyzambia', '...   
190  {'0': ['http://twitter.com/usembassyharare', '...   

                                            Post_Url_1  \
0                    https://af.usembassy.gov/embassy/   
1             https://al.usembassy.gov/embassy/tirana/   
2                    https://dz.usembassy.gov/embassy/   
3                    https://ao.usembassy.gov/embassy/   
4                    https://ar.usembassy.gov/embassy/   
..                                                 ...   
186                  https://ve.usembassy.gov/interim/   
187  https://vn.usembassy.gov/embassy-consulate/emb...   
188                  https://ye.usembassy.gov/embassy/   
189          https://zm.usembassy.gov/embassy/embassy/   
190           https://zw.usembassy.gov/embassy/harare/   

                                            Post_Url_2 Post_Url_3 Post_Url_4  \
0                                                  nan        nan        nan   
1                                                  nan        nan        nan   
2                                                  nan        nan        nan   
3                                                  nan        nan        nan   
4                                                  nan        nan        nan   
..                                                 ...        ...        ...   
186                                                nan        nan        nan   
187  https://vn.usembassy.gov/embassy-consulate/ho-...        nan        nan   
188                                                nan        nan        nan   
189                                                nan        nan        nan   
190                                                nan        nan        nan   

    Post_Url_5 Post_Url_6  ... Post_7 Post_8 Post_9 Post_10 Social_2  \
0          nan        nan  ...   None   None   None    None     {'0'   
1          nan        nan  ...   None   None   None    None     {'0'   
2          nan        nan  ...   None   None   None    None     {'0'   
3          nan        nan  ...   None   None   None    None     {'0'   
4          nan        nan  ...   None   None   None    None     {'0'   
..         ...        ...  ...    ...    ...    ...     ...      ...   
186        nan        nan  ...   None   None

In [198]:
country_data = pd.read_json('../data/Final_data.json')
country_data["Country"] = country_data["Country"].str.title()
country_data["Post"] = country_data["Post"].str.title()
country_data["ID"] = range(0,len(country_data))
post_data = pd.read_csv('../data/Transposed_csv.csv', encoding="latin1")
#post_data["Country"] = post_data.Country.str.replace('https://www.usembassy.gov/','')
post_data["Country"] = post_data["Country"].str.title()
#post_data["Country"] = post_data.Country.str.replace('/','')
#post_data["Posts"] = post_data.Posts.str.replace('embassy-consulates','')
#post_data["Posts"] = post_data.Posts.str.replace('embassy','')
#post_data["Posts"] = post_data.Posts.str.replace('consulates','')
#post_data["Posts"] = post_data.Posts.str.replace('consulate','')
#post_data["Posts"] = post_data.Posts.str.replace('v/','')
#post_data["Posts"] = post_data.Posts.str.replace('/','')
#post_data["Posts"] = post_data.Posts.str.replace('-',' ')
#post_data["Country"] = post_data.Country.str.replace('-',' ')
#post_data["Country"] = post_data.Country.str.replace('timor leste','timor-leste')
post_data["Posts"] = post_data["Posts"].str.title()
post_data = post_data.rename(columns={"Posts":"Post"})
post_data = post_data.fillna('')
final_merge = pd.merge(country_data, post_data, how="left",on=["Country", "Post"])
#final_merge = final_merge.fillna('')
#final_merge = final_merge.drop(["Unnamed: 0"], axis=1)
final_merge.to_csv('Data_With_Social.csv')
final_merge

Status Bureau               Country       Post   Latitude  Longitude  \
0     Active     AF         Cote D'Ivoire    Abidjan   5.334631  -3.975871   
1     Active     AF         Cote D'Ivoire    Abidjan   5.334631  -3.975871   
2     Active     AF         Cote D'Ivoire    Abidjan   5.334631  -3.975871   
3     Active    NEA  United Arab Emirates  Abu Dhabi  24.424022  54.433639   
4     Active    NEA  United Arab Emirates  Abu Dhabi  24.424022  54.433639   
...      ...    ...                   ...        ...        ...        ...   
1062  Active    EUR               Armenia    Yerevan  40.165129  44.482992   
1063  Active    EUR               Croatia     Zagreb  45.744114  16.003460   
1064  Active    EUR               Croatia     Zagreb  45.744114  16.003460   
1065  Active    EUR               Croatia     Zagreb  45.744114  16.003460   
1066  Active    EUR               Croatia     Zagreb  45.744114  16.003460   

     Languages_x   ID     Languages_y  \
0         French    0       FranÃ§ais   
1         French    0       FranÃ§ais   
2         French    0       FranÃ§ais   
3         Arabic    1                   
4         Arabic    1                   
...          ...  ...             ...   
1062    Armenian  273  ÕÕ¡ÕµÕ¥ÖÕ¥Õ¶   
1063    Croatian  274        Hrvatski   
1064    Croatian  274        Hrvatski   
1065    Croatian  274        Hrvatski   
1066    Croatian  274        Hrvatski   

                                                 Social  \
0                      https://twitter.com/USEmbAbidjan   
1     https://www.facebook.com/pages/US-Embassy-Abid...   
2     http://www.youtube.com/channel/UCOMiNfCDecFMap...   
3                          https://twitter.com/USAinUAE   
4                     https://www.facebook.com/USAinUAE   
...                                                 ...   
1062            https://www.instagram.com/usembarmenia/   
1063                 http://www.twitter.com/USEmbZagreb   
1064           http://www.facebook.com/zagreb.usembassy   
1065        http://www.youtube.com/user/usembassyzagreb   
1066        https://www.instagram.com/usembassycroatia/   

                                            Embassy_Url  
0             https://ci.usembassy.gov/embassy/embassy/  
1             https://ci.usembassy.gov/embassy/embassy/  
2             https://ci.usembassy.gov/embassy/embassy/  
3     https://ae.usembassy.gov/embassy-consulates/ab...  
4     https://ae.usembassy.gov/embassy-consulates/ab...  
...                                                 ...  
1062                  https://am.usembassy.gov/embassy/  
1063           https://hr.usembassy.gov/embassy/zagreb/  
1064           https://hr.usembassy.gov/embassy/zagreb/  
1065           https://hr.usembassy.gov/embassy/zagreb/  
1066           https://hr.usembassy.gov/embassy/zagreb/  

[1067 rows x 11 columns]

In [208]:
#pivot_table = final_merge.pivot_table(['Social','Embassy_Url'], ['ID', 'Status', 'Bureau', 'Country', 'Post','Latitude','Longitude', 'Languages_y', 'Languages_x'], aggfunc=', '.join)
#pivot_table.to_csv("test_data.csv")
#pivot_table

Embassy_Url  \
ID  Status Bureau Country              Post          Latitude  Longitude  Languages_y      Languages_x                                                      
0   Active AF     Cote D'Ivoire        Abidjan       5.334631  -3.975871  FranÃ§ais        French       https://ci.usembassy.gov/embassy/embassy/, htt...   
1   Active NEA    United Arab Emirates Abu Dhabi     24.424022  54.433639                  Arabic       https://ae.usembassy.gov/embassy-consulates/ab...   
2   Active AF     Nigeria              Abuja         9.041790   7.477239                   English      https://ng.usembassy.gov/embassy-consulate/abu...   
3   Active AF     Ghana                Accra         5.578913  -0.170634                   English      https://gh.usembassy.gov/embassy/, https://gh....   
4   Active EUR    Turkey               Adana         36.983267  35.385076 TÃ¼rkÃ§e         Turkish      https://tr.usembassy.gov/embassy-consulates/ad...   
...                                                                                                                                                   ...   
272 Active EUR    Russia               Yekaterinburg 56.833362  60.610115 Ð ÑÑÑÐºÐ¸Ð155 Russian      https://ru.usembassy.gov/embassy-consulates/ye...   
                                                                          Ð ÑÑÑÐºÐ¸Ð156 Russian      https://ru.usembassy.gov/embassy-consulates/ye...   
                                                                          Ð ÑÑÑÐºÐ¸Ð157 Russian      https://ru.usembassy.gov/embassy-consulates/ye...   
273 Active EUR    Armenia              Yerevan       40.165129  44.482992 ÕÕ¡ÕµÕ¥ÖÕ¥Õ¶   Armenian     https://am.usembassy.gov/embassy/, https://am....   
274 Active EUR    Croatia              Zagreb        45.744114  16.003460 Hrvatski         Croatian     https://hr.usembassy.gov/embassy/zagreb/, http...   

                                                                                                                                                   Social  
ID  Status Bureau Country              Post          Latitude  Longitude  Languages_y      Languages_x                                                     
0   Active AF     Cote D'Ivoire        Abidjan       5.334631  -3.975871  FranÃ§ais        French       https://twitter.com/USEmbAbidjan, https://www....  
1   Active NEA    United Arab Emirates Abu Dhabi     24.424022  54.433639                  Arabic       https://twitter.com/USAinUAE, https://www.face...  
2   Active AF     Nigeria              Abuja         9.041790   7.477239                   English      https://twitter.com/USinNigeria, https://www.f...  
3   Active AF     Ghana                Accra         5.578913  -0.170634                   English      http://twitter.com/USEmbassyGhana, http://face...  
4   Active EUR    Turkey               Adana         36.983267  35.385076 TÃ¼rkÃ§e         Turkish      http://instagram.com/abdbaskonsoloslugu, http:...  
...                                                                                                                                                   ...  
272 Active EUR    Russia               Yekaterinburg 56.833362  60.610115 Ð ÑÑÑÐºÐ¸Ð155 Russian            http://www.flickr.com/photos/yekatconsulate  
                                                                          Ð ÑÑÑÐºÐ¸Ð156 Russian                  http://instagram.com/usconsulateyekat  
                                                                          Ð ÑÑÑÐºÐ¸Ð157 Russian                         http://vk.com/usconsulateyekat  
273 Active EUR    Armenia              Yerevan       40.165129  44.482992 ÕÕ¡ÕµÕ¥ÖÕ¥Õ¶   Armenian     http://twitter.com/usembarmenia, https://www.f...  
274 Active EUR    Croatia              Zagreb        45.744114  16.003460 Hrvatski         Croatian     http://www.twitter.com/USEmbZagreb, http://www...  

[314 rows x 2 columns]

In [212]:
def f(df):
    return pd.DataFrame(np.sort(df.values, 0)[[-1]], [df.name], df.columns)

final = final_merge.set_index(
    'ID', append=True
).groupby(level='ID', group_keys=False).apply(f)

final.to_csv("move_to.csv")

In [167]:
country_data

Status Bureau               Country           Post   Latitude  \
0    Active     AF         Cote D'Ivoire        Abidjan   5.334631   
1    Active    NEA  United Arab Emirates      Abu Dhabi  24.424022   
2    Active     AF               Nigeria          Abuja   9.041790   
3    Active     AF                 Ghana          Accra   5.578913   
4    Active    EUR                Turkey          Adana  36.983267   
..      ...    ...                   ...            ...        ...   
270  Active    EAP                 China          Wuhan  30.355113   
271  Active     AF              Cameroon        Yaounde   3.899973   
272  Active    EUR                Russia  Yekaterinburg  56.833362   
273  Active    EUR               Armenia        Yerevan  40.165129   
274  Active    EUR               Croatia         Zagreb  45.744114   

      Longitude        Languages  
0     -3.975871           French  
1     54.433639           Arabic  
2      7.477239          English  
3     -0.170634          English  
4     35.385076          Turkish  
..          ...              ...  
270  114.155370         Mandarin  
271   11.499179  English, French  
272   60.610115          Russian  
273   44.482992         Armenian  
274   16.003460         Croatian  

[275 rows x 7 columns]

In [265]:
import xlrd
from collections import OrderedDict
import json
wb = xlrd.open_workbook("answer.xlsx")
sh = wb.sheet_by_index(0)
data_list = []
for rownum in range(1, sh.nrows):
    data = OrderedDict()
    row_values = sh.row_values(rownum)
    data['Status'] = row_values[0]
    data['Bureau'] = row_values[1]
    data['Country'] = row_values[2]
    data['Post'] = row_values[3]
    data['Latitude'] = row_values[4]
    data['Longitude'] = row_values[5]
    data['Languages'] = row_values[6]
    data['Social'] = row_values[7]
    data['Social'] = row_values[9]
    data['Embassy_Url'] = row_values[10]
    data_list.append(data)
with open("Final_Data.json", "w", encoding="utf-8") as writeJsonfile:
      json.dump(data_list, writeJsonfile,ensure_ascii=False, indent=4,default=str)